In [9]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from geopy import Nominatim
from geopy.extra.rate_limiter import RateLimiter
from tqdm.auto import tqdm

In [7]:
aed = pd.read_parquet('data/aed_locations.parquet.gzip')
aed['concat_address'] = aed['address'] + ' ' + aed['number'].fillna('').astype(str).apply(lambda x: str(int(float(x))) if x.strip() and '.' in x else x) + ', ' + aed['province'] + ', ' + aed['postal_code'].fillna('').astype(str).apply(lambda x: str(int(float(x))) if x.strip() and '.' in x else x) + ', Belgique'
aed['concat_address']

0          Blvd. Fr. Roosevelt 24, Hainaut, 7060, Belgique
1                Ch. De Wégimont 76, Liège, 4630, Belgique
2            Place Saint - Lambert , Liège, 4020, Belgique
3                    Rue du Doyard , Liège, 4990, Belgique
4               Fond Saint Servais , Liège, 4000, Belgique
                               ...                        
15222     Nekkerspoel-Borcht 19, Antwerpen, 2800, Belgique
15223    Nieuwe Dreef  17, Oost-Vlaanderen, 9160, Belgique
15224    Panterschipstraat  207, Oost-Vlaanderen, 9000,...
15225    Albert Leemansplein 20, Bruxelles-Brussel, 105...
15226            rue Saint-Donat 18, Namur, 5640, Belgique
Name: concat_address, Length: 15227, dtype: object

In [20]:
locator = Nominatim(user_agent="wigsyo")
geocode = RateLimiter(locator.geocode, min_delay_seconds=0.1)
aed['location_geo'] = aed['concat_address']*0
for i in tqdm(range(len(aed))):
    aed['location_geo'].iloc[i] = geocode(aed['concat_address'].iloc[i])

  0%|          | 0/15227 [00:00<?, ?it/s]

/tmp/ipykernel_14020/3274124550.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  aed['location_geo'].iloc[i] = geocode(aed['concat_address'].iloc[i])
/tmp/ipykernel_14020/3274124550.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  aed['location_geo'].iloc[i] = geocode(aed['concat_address'].iloc[i])
/tmp/ipykernel_14020/3274124550.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  aed['location_geo'].iloc[i] = geocode(aed['concat

In [28]:
aed["coords"].tolist()

[None,
 None,
 (50.6449558, 5.5745133, 0.0),
 (50.2850428, 5.7859495, 0.0),
 (50.6465715, 5.5699752, 0.0),
 (50.6379967, 5.573779991887541, 0.0),
 (50.3806158, 5.680907587084247, 0.0),
 (50.57723315, 5.3230382796615805, 0.0),
 None,
 (50.643467650000005, 5.572142917858384, 0.0),
 (50.63699855, 5.565328490517242, 0.0),
 (50.8428283, 4.3844261, 0.0),
 (51.1971308, 4.4300786, 0.0),
 (50.998105800000005, 4.8781133289798575, 0.0),
 (50.8829048, 4.3319445, 0.0),
 None,
 None,
 (49.6737934, 5.8199363, 0.0),
 (50.831942299999994, 4.328980253636651, 0.0),
 (51.2341134, 4.3204443961465735, 0.0),
 (50.88091925, 4.442448069989586, 0.0),
 (50.759496850000005, 5.759718511368475, 0.0),
 (50.731173, 5.880948698706895, 0.0),
 (50.73746745, 5.823412607364022, 0.0),
 (50.93198845, 5.571475840364583, 0.0),
 (50.7625781, 5.8844909, 0.0),
 (50.74940645, 5.812551332425043, 0.0),
 None,
 (50.97965045, 5.472422009968787, 0.0),
 (50.8755861, 4.3539073, 0.0),
 None,
 (50.63892735, 5.574213550178143, 0.0),
 (50.6

In [32]:
aed['coords'] = aed['location_geo'].apply(lambda loc: tuple(loc.point) if loc else None)
aed[['lat', 'lon', 'alt']] = 0
for i in range(len(aed)):
    if aed["coords"][i] is not None:
        aed['lat'][i] = aed["coords"][i][0]
        aed['lon'][i] = aed["coords"][i][1]
        aed['alt'][i] = aed["coords"][i][2]
    else:
        aed['lat'][i] = None
        aed['lon'][i] = None
        aed['alt'][i] = None
print(aed[['lat', 'lon', 'alt']])
aed.to_csv('aed_geocoords.csv', index=False)


/tmp/ipykernel_14020/376965807.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  aed['lat'][i] = None
/tmp/ipykernel_14020/376965807.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  aed['lon'][i] = None
/tmp/ipykernel_14020/376965807.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  aed['alt'][i] = None


             lat       lon  alt
0            NaN       NaN  NaN
1            NaN       NaN  NaN
2      50.644956  5.574513  0.0
3      50.285043  5.785950  0.0
4      50.646572  5.569975  0.0
...          ...       ...  ...
15222  51.025077  4.503698  0.0
15223  51.097802  3.911744  0.0
15224        NaN       NaN  NaN
15225  50.821748  4.362927  0.0
15226  50.266475  4.459041  0.0

[15227 rows x 3 columns]


In [18]:
for i in tqdm(range(len(aed))):
    if aed['location_geo'].iloc[i]:
        print(aed['location_geo'].iloc[i].point)
print(aed["location_geo"])

  0%|          | 0/15227 [00:00<?, ?it/s]

50 38m 41.8409s N, 5 34m 28.2479s E
50 17m 6.15408s N, 5 47m 9.4182s E
50 38m 47.6574s N, 5 34m 11.9107s E
50 38m 16.7881s N, 5 34m 25.608s E
50 22m 50.2169s N, 5 40m 51.2673s E
50 34m 38.0393s N, 5 19m 22.9378s E
50 38m 36.4835s N, 5 34m 19.7145s E
50 38m 13.1948s N, 5 33m 55.1826s E
50 50m 34.1819s N, 4 23m 3.93396s E
51 11m 49.6709s N, 4 25m 48.283s E
50 59m 53.1809s N, 4 52m 41.208s E
50 52m 58.4573s N, 4 19m 55.0002s E
49 40m 25.6562s N, 5 49m 11.7707s E
50 49m 54.9923s N, 4 19m 44.3289s E
51 14m 2.80824s N, 4 19m 13.5998s E
50 52m 51.3093s N, 4 26m 32.8131s E
50 45m 34.1887s N, 5 45m 34.9866s E
50 43m 52.2228s N, 5 52m 51.4153s E
50 44m 14.8828s N, 5 49m 24.2854s E
50 55m 55.1584s N, 5 34m 17.313s E
50 45m 45.2812s N, 5 53m 4.16724s E
50 44m 57.8632s N, 5 48m 45.1848s E
50 58m 46.7416s N, 5 28m 20.7192s E
50 52m 32.11s N, 4 21m 14.0663s E
50 38m 20.1385s N, 5 34m 27.1688s E
50 40m 17.8698s N, 5 38m 24.0151s E
50 39m 28.1844s N, 5 29m 36.5143s E
50 37m 23.2311s N, 5 42m 40.9594s E

AttributeError: 'float' object has no attribute 'point'